### Neo4j

First we load the dependencies for NER and relation models as well as the NER model itself that has been previously fine-tuned

#### Import libraries

In [27]:
import spacy
import pandas as pd
import hashlib
nlp = spacy.load(".rel_component/project.yml")
import random

OSError: [E050] Can't find model '.rel_component/project.yml'. It doesn't seem to be a Python package or a valid path to a data directory.

Load the jobs dataset from which we want to extract the entities and relations

In [3]:
df= pd.read_csv("assets/Train_rev1.csv",header= None)
df

/home/becode/.local/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3457: DtypeWarning: Columns (0,10) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


0                                                  1   \
0             Id                                              Title   
1       12612628                        Engineering Systems Analyst   
2       12612830                            Stress Engineer Glasgow   
3       12612844                   Modelling and simulation analyst   
4       12613049  Engineering Systems Analyst / Mathematical Mod...   
...          ...                                                ...   
244764  72705211                                 TEACHER OF SCIENCE   
244765  72705212                TEACHER OF BUSINESS STUDIES AND ICT   
244766  72705213                                    ENGLISH TEACHER   
244767  72705216                                    SUPPLY TEACHERS   
244768  72705235                                         Accountant   

                                                       2   \
0                                         FullDescription   
1       Engineering Systems Analyst Dorking Surrey Sal...   
2       Stress Engineer Glasgow Salary **** to **** We...   
3       Mathematical Modeller / Simulation Analyst / O...   
4       Engineering Systems Analyst / Mathematical Mod...   
...                                                   ...   
244764  Position: Qualified Teacher Subject/Specialism...   
244765  Position: Qualified Teacher or NQT Subject/Spe...   
244766  Position: Qualified Teacher Subject/Specialism...   
244767  Position: Qualified Teacher Subject/Specialism...   
244768  This entrepreneurial and growing private equit...   

                                       3                   4             5   \
0                             LocationRaw  LocationNormalized  ContractType   
1                 Dorking, Surrey, Surrey             Dorking           NaN   
2             Glasgow, Scotland, Scotland             Glasgow           NaN   
3       Hampshire, South East, South East           Hampshire           NaN   
4          Surrey, South East, South East              Surrey           NaN   
...                                   ...                 ...           ...   
244764                            Swindon             Swindon           NaN   
244765                            Swindon             Swindon           NaN   
244766                            Swindon             Swindon           NaN   
244767                          Wiltshire           Wiltshire           NaN   
244768                            Hitchin             Hitchin           NaN   

                  6                             7                 8   \
0       ContractTime                       Company          Category   
1          permanent  Gregory Martin International  Engineering Jobs   
2          permanent  Gregory Martin International  Engineering Jobs   
3          permanent  Gregory Martin International  Engineering Jobs   
4          permanent  Gregory Martin International  Engineering Jobs   
...              ...                           ...               ...   
244764      contract                           NaN     Teaching Jobs   
244765      contract                           NaN     Teaching Jobs   
244766      contract                           NaN     Teaching Jobs   
244767      contract                           NaN     Teaching Jobs   
244768     permanent                           NaN     Teaching Jobs   

                                            9                 10  \
0                                    SalaryRaw  SalaryNormalized   
1                   20000 - 30000/annum 20-30K             25000   
2                   25000 - 35000/annum 25-35K             30000   
3                   20000 - 40000/annum 20-40K             30000   
4       25000 - 30000/annum 25K-30K negotiable             27500   
...                                        ...               ...   
244764                      450 - 500 per week             22800   
244765                      450 - 500 per week             22800   
24

In [4]:
# import pandas library
def get_all_documents(df):
    documents= []
    for index, row in df.iterrows():
        documents.append(str(row[0]))
    return documents
    
documents= get_all_documents(df)
documents = documents[:]
documents

['Id',
 '12612628',
 '12612830',
 '12612844',
 '12613049',
 '12613647',
 '13179816',
 '14131336',
 '14663196',
 '14663197',
 '15395797',
 '19047429',
 '20199757',
 '20638787',
 '20638788',
 '20797143',
 '22579462',
 '22581547',
 '22933091',
 '23528672',
 '23529949',
 '23530231',
 '24104334',
 '24835524',
 '24835548',
 '24854800',
 '25337172',
 '25434785',
 '25452606',
 '25452680',
 '25556432',
 '25892031',
 '27527047',
 '27527050',
 '27527063',
 '27527077',
 '27739522',
 '27739539',
 '27740574',
 '27754996',
 '28059808',
 '28216382',
 '28539205',
 '28821429',
 '29107908',
 '29570321',
 '29570883',
 '29570885',
 '29571472',
 '29571506',
 '29571632',
 '29650985',
 '30192171',
 '30292879',
 '30502258',
 '30502270',
 '30502285',
 '30502291',
 '31301427',
 '31301430',
 '31340140',
 '31347600',
 '31559355',
 '31559362',
 '31559397',
 '31559481',
 '31794403',
 '31935432',
 '31989124',
 '31989135',
 '32211674',
 '32233421',
 '32359589',
 '32417995',
 '32423204',
 '32621550',
 '32621604',
 '326

Extract entities from the jobs dataset

In [5]:
#import hashlib module
def extract_ents(documents, nlp):
    """ The hashlib module is an interface for hashing messages easily"""
    docs= list()
    for doc in nlp.pipe(documents, disable=["tagger", "parser"]):
        dictionary=dict.fromkeys(["text", "annotations"])
        dictionary["text"]= str(doc)
        dictionary['text_sha256'] =  hashlib.sha256(dictionary["text"].encode('utf-8')).hexdigest()
        annotations=[]
        
        
        for item in doc.ents:
            ent_id= hashlib.sha256(str(item.text).encode('utf-8')).hexdigest()
            ent= {"start": item.start_char, "end": item.end_char, "label": item.label_,
                  "label_upper": item.label_.upper(), "text": item.text, "id": ent_id}
            if item.label== "EXPERIENCE":
                ent["years"]= int(item.text[0])
                
            annotations.append(ent)
            
        dictionary["annotations"] = annotations
        docs.append(dictionary)
    
    #print(annotations)
    return docs

extract_ents(documents, nlp)

[2022-01-11 10:25:46,547] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token 'I'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,548] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token 'd'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,549] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '12612628'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,550] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '12612830'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,5

[2022-01-11 10:25:46,609] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '27527050'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,616] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '27527063'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,618] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '27527077'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,620] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '27739522'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01

[2022-01-11 10:25:46,678] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '31935432'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,679] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '31989124'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,681] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '31989135'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,682] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '32211674'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01

[2022-01-11 10:25:46,722] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '35584733'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,723] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '35740450'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,726] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '36050971'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,727] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '36757414'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01

[2022-01-11 10:25:46,818] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '41406170'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,819] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '41406171'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,821] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '41783094'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:25:46,822] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '41879934'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01

...

[2022-01-11 10:26:54,251] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071007'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,252] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071009'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,254] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071015'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,254] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071017'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01

[2022-01-11 10:26:54,321] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071204'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,322] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071210'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,324] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071212'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,328] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071215'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01

[2022-01-11 10:26:54,371] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071319'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,372] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071320'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,373] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071336'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,377] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68071339'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01

[2022-01-11 10:26:54,416] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68072014'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,417] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68072037'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,417] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68072166'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01-11 10:26:54,419] [WARNING] [W108] The rule-based lemmatizer did not find POS annotation for the token '68072256'. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
[2022-01

KeyboardInterrupt: 

still to work on

### Resources

* hashlib: https://docs.python.org/3/library/hashlib.html


* roadmap: https://towardsdatascience.com/how-to-build-a-knowledge-graph-with-neo4j-and-transformers-72b9471d6969